# Regression Notebook - `Boston House Price (Sales Prediction).ipynb`

## Add JupyterHelper and Download Dependencies

In [1]:
%jars ../libs/JupyterHelper-1.0-SNAPSHOT-jar-with-dependencies.jar

In [2]:
%%loadFromPOM

<properties>
    <deepnetts.version>1.12</deepnetts.version>
    <visrec.version>1.0.1</visrec.version>
</properties>

<dependency>
  <groupId>javax.visrec</groupId>
  <artifactId>visrec-api</artifactId>
  <version>1.0.1</version>
</dependency>
<dependency>
  <groupId>javax.visrec</groupId>
  <artifactId>visrec-ri</artifactId>
  <version>1.0.1</version>
  <type>jar</type>
  <exclusions>
      <exclusion>
          <groupId>com.deepnetts</groupId>
          <artifactId>deepnetts-core</artifactId>
      </exclusion>
  </exclusions>
</dependency>
<dependency>
    <groupId>com.deepnetts</groupId>
    <artifactId>deepnetts-core</artifactId>
    <version>${deepnetts.version}</version>
</dependency>

## Imports

In [16]:
import java.io.ObjectInputStream;

import deepnetts.data.norm.MaxNormalizer;
import deepnetts.util.Tensors;
import deepnetts.data.DataSets;
import deepnetts.data.*;
import deepnetts.eval.Evaluators;
import javax.visrec.ml.eval.EvaluationMetrics;
import deepnetts.net.FeedForwardNetwork;
import deepnetts.net.layers.activation.ActivationType;
import deepnetts.net.loss.LossType;
import deepnetts.util.Tensor;
import java.io.IOException;
import javax.visrec.ml.data.DataSet;
import deepnetts.net.train.opt.OptimizerType;
import deepnetts.util.FileIO;
import org.knowm.xchart.*;
import org.knowm.xchart.XYSeries.*;
import org.knowm.xchart.style.*;

import java.awt.image.*;

import ch.bytecrowd.JupyterHelper;

## Download Dataset

In [4]:
var BOSTON_HOUSES_BASEURL   = "https://raw.githubusercontent.com/deepnetts/deepnetts-communityedition/community-visrec/deepnetts-examples/datasets/bostonhouse.txt";
var BOSTON_HOUSES_FILE_ORIG = "/tmp/bostonhouse_orig.txt";
var BOSTON_HOUSES_FILE = "/tmp/bostonhouse.txt";
JupyterHelper.downloadFile(BOSTON_HOUSES_BASEURL, BOSTON_HOUSES_FILE_ORIG);

## Prepare DataSet

In [5]:
JupyterHelper.executeOsCommand("head -n 2 " + BOSTON_HOUSES_FILE_ORIG);

Executing OS command: sh -c head -n 2 /tmp/bostonhouse_orig.txt

0.00632,18.00,2.310,0,0.5380,6.5750,65.20,4.0900,1,296.0,15.30,396.90,4.98,24.00
0.02731,0.00,7.070,0,0.4690,6.4210,78.90,4.9671,2,242.0,17.80,396.90,9.14,21.60



**remove first row**  
will be used for later step (Run raw data aginst the model)

In [6]:
JupyterHelper.executeOsCommand(
    "tail -n +2 " + BOSTON_HOUSES_FILE_ORIG + " > " + BOSTON_HOUSES_FILE
);

Executing OS command: sh -c tail -n +2 /tmp/bostonhouse_orig.txt > /tmp/bostonhouse.txt



In [7]:
int inputsNum = 13;
int outputsNum = 1;
String csvFilename = BOSTON_HOUSES_FILE;

// load and create data set from csv file
DataSet dataSet = DataSets.readCsv(csvFilename , inputsNum, outputsNum, true);

**normalize data**

In [9]:
var normalizer = new MaxNormalizer(dataSet);
normalizer.normalize(dataSet);

**split train and test data**

In [10]:
DataSet[] trainAndTestSet = dataSet.split(0.6);

## Create a Neuronal Network

In [11]:
 // create neural network using network specific builder
FeedForwardNetwork neuralNet = FeedForwardNetwork.builder()
        .addInputLayer(inputsNum)//inputsNum)
        .addFullyConnectedLayer(3, ActivationType.TANH)
        .addOutputLayer(outputsNum, ActivationType.LINEAR)
        .lossFunction(LossType.MEAN_SQUARED_ERROR)
        .build();

## Train the Neuronal Network

In [230]:
var trainer = neuralNet.getTrainer();
trainer.setMaxError(0.001f);
trainer.setLearningRate(0.1f);
trainer.setMomentum(0.09f);
trainer.setOptimizer(OptimizerType.MOMENTUM);
trainer.train(trainAndTestSet[0]);

------------------------------------------------------------------------------------------------------------------------------------------------
TRAINING NEURAL NETWORK
------------------------------------------------------------------------------------------------------------------------------------------------
Epoch:1, Time:0ms, TrainError:0.013289829, TrainErrorChange:0.013289829, TrainAccuracy: 0.75165564
Epoch:2, Time:0ms, TrainError:0.009161065, TrainErrorChange:-0.0041287635, TrainAccuracy: 0.81125826
Epoch:3, Time:1ms, TrainError:0.008076497, TrainErrorChange:-0.001084568, TrainAccuracy: 0.8344371
Epoch:4, Time:0ms, TrainError:0.0075152023, TrainErrorChange:-5.612951E-4, TrainAccuracy: 0.8476821
Epoch:5, Time:0ms, TrainError:0.007166095, TrainErrorChange:-3.491072E-4, TrainAccuracy: 0.8543046
Epoch:6, Time:0ms, TrainError:0.0069214376, TrainErrorChange:-2.446575E-4, TrainAccuracy: 0.86092716
Epoch:7, Time:0ms, TrainError:0.006735544, TrainErrorChange:-1.8589338E-4, TrainAccurac

Epoch:79, Time:1ms, TrainError:0.004518531, TrainErrorChange:-9.461772E-6, TrainAccuracy: 0.87086093
Epoch:80, Time:0ms, TrainError:0.004509183, TrainErrorChange:-9.347685E-6, TrainAccuracy: 0.87086093
Epoch:81, Time:1ms, TrainError:0.0044999477, TrainErrorChange:-9.23546E-6, TrainAccuracy: 0.87086093
Epoch:82, Time:0ms, TrainError:0.0044908132, TrainErrorChange:-9.134412E-6, TrainAccuracy: 0.87086093
Epoch:83, Time:1ms, TrainError:0.0044817734, TrainErrorChange:-9.039883E-6, TrainAccuracy: 0.87086093
Epoch:84, Time:0ms, TrainError:0.004472822, TrainErrorChange:-8.951407E-6, TrainAccuracy: 0.8741722
Epoch:85, Time:0ms, TrainError:0.0044639464, TrainErrorChange:-8.875504E-6, TrainAccuracy: 0.8741722
Epoch:86, Time:0ms, TrainError:0.0044551454, TrainErrorChange:-8.800998E-6, TrainAccuracy: 0.8741722
Epoch:87, Time:0ms, TrainError:0.004446407, TrainErrorChange:-8.7386E-6, TrainAccuracy: 0.8741722
Epoch:88, Time:0ms, TrainError:0.004437724, TrainErrorChange:-8.68272E-6, TrainAccuracy: 0.87

Epoch:160, Time:0ms, TrainError:0.0037323916, TrainErrorChange:-1.0362361E-5, TrainAccuracy: 0.86754966
Epoch:161, Time:0ms, TrainError:0.0037220842, TrainErrorChange:-1.0307413E-5, TrainAccuracy: 0.87086093
Epoch:162, Time:0ms, TrainError:0.003711831, TrainErrorChange:-1.0253163E-5, TrainAccuracy: 0.87086093
Epoch:163, Time:0ms, TrainError:0.0037016347, TrainErrorChange:-1.0196352E-5, TrainAccuracy: 0.87086093
Epoch:164, Time:1ms, TrainError:0.003691494, TrainErrorChange:-1.0140706E-5, TrainAccuracy: 0.87086093
Epoch:165, Time:0ms, TrainError:0.003681409, TrainErrorChange:-1.0085059E-5, TrainAccuracy: 0.87086093
Epoch:166, Time:1ms, TrainError:0.0036713849, TrainErrorChange:-1.0024058E-5, TrainAccuracy: 0.8741722
Epoch:167, Time:0ms, TrainError:0.0036614158, TrainErrorChange:-9.96911E-6, TrainAccuracy: 0.8741722
Epoch:168, Time:0ms, TrainError:0.0036515056, TrainErrorChange:-9.9102035E-6, TrainAccuracy: 0.8741722
Epoch:169, Time:0ms, TrainError:0.0036416582, TrainErrorChange:-9.847339

Epoch:241, Time:0ms, TrainError:0.0030658173, TrainErrorChange:-6.331131E-6, TrainAccuracy: 0.8642384
Epoch:242, Time:1ms, TrainError:0.003059538, TrainErrorChange:-6.2792096E-6, TrainAccuracy: 0.8642384
Epoch:243, Time:0ms, TrainError:0.003053307, TrainErrorChange:-6.2310137E-6, TrainAccuracy: 0.8642384
Epoch:244, Time:1ms, TrainError:0.003047126, TrainErrorChange:-6.180955E-6, TrainAccuracy: 0.8642384
Epoch:245, Time:0ms, TrainError:0.003040995, TrainErrorChange:-6.1311293E-6, TrainAccuracy: 0.8642384
Epoch:246, Time:0ms, TrainError:0.003034915, TrainErrorChange:-6.0799066E-6, TrainAccuracy: 0.86754966
Epoch:247, Time:0ms, TrainError:0.0030288831, TrainErrorChange:-6.0319435E-6, TrainAccuracy: 0.86754966
Epoch:248, Time:0ms, TrainError:0.0030229033, TrainErrorChange:-5.9797894E-6, TrainAccuracy: 0.86754966
Epoch:249, Time:0ms, TrainError:0.0030169745, TrainErrorChange:-5.9287995E-6, TrainAccuracy: 0.86754966
Epoch:250, Time:0ms, TrainError:0.0030110944, TrainErrorChange:-5.880138E-6,

Epoch:321, Time:0ms, TrainError:0.0027073347, TrainErrorChange:-3.0472875E-6, TrainAccuracy: 0.8576159
Epoch:322, Time:0ms, TrainError:0.0027043128, TrainErrorChange:-3.021909E-6, TrainAccuracy: 0.8576159
Epoch:323, Time:0ms, TrainError:0.0027013153, TrainErrorChange:-2.9974617E-6, TrainAccuracy: 0.8576159
Epoch:324, Time:0ms, TrainError:0.0026983419, TrainErrorChange:-2.9734802E-6, TrainAccuracy: 0.8576159
Epoch:325, Time:1ms, TrainError:0.002695394, TrainErrorChange:-2.9478688E-6, TrainAccuracy: 0.8576159
Epoch:326, Time:0ms, TrainError:0.0026924692, TrainErrorChange:-2.9248185E-6, TrainAccuracy: 0.8576159
Epoch:327, Time:1ms, TrainError:0.002689567, TrainErrorChange:-2.902234E-6, TrainAccuracy: 0.8576159
Epoch:328, Time:0ms, TrainError:0.0026866877, TrainErrorChange:-2.8791837E-6, TrainAccuracy: 0.8576159
Epoch:329, Time:0ms, TrainError:0.0026838304, TrainErrorChange:-2.8572977E-6, TrainAccuracy: 0.8576159
Epoch:330, Time:0ms, TrainError:0.0026809974, TrainErrorChange:-2.8330833E-6,

...

Epoch:99130, Time:1ms, TrainError:0.001474869, TrainErrorChange:-1.1641532E-10, TrainAccuracy: 0.8807947
Epoch:99131, Time:0ms, TrainError:0.00147487, TrainErrorChange:1.0477379E-9, TrainAccuracy: 0.8807947
Epoch:99132, Time:1ms, TrainError:0.0014748686, TrainErrorChange:-1.3969839E-9, TrainAccuracy: 0.8807947
Epoch:99133, Time:0ms, TrainError:0.0014748679, TrainErrorChange:-6.9849193E-10, TrainAccuracy: 0.8807947
Epoch:99134, Time:1ms, TrainError:0.001474868, TrainErrorChange:1.1641532E-10, TrainAccuracy: 0.8807947
Epoch:99135, Time:0ms, TrainError:0.0014748679, TrainErrorChange:-1.1641532E-10, TrainAccuracy: 0.8807947
Epoch:99136, Time:0ms, TrainError:0.0014748677, TrainErrorChange:-2.3283064E-10, TrainAccuracy: 0.8807947
Epoch:99137, Time:0ms, TrainError:0.0014748673, TrainErrorChange:-3.4924597E-10, TrainAccuracy: 0.8807947
Epoch:99138, Time:0ms, TrainError:0.0014748664, TrainErrorChange:-9.313226E-10, TrainAccuracy: 0.8807947
Epoch:99139, Time:0ms, TrainError:0.0014748663, TrainEr

Epoch:99209, Time:0ms, TrainError:0.0014748452, TrainErrorChange:4.656613E-10, TrainAccuracy: 0.8807947
Epoch:99210, Time:0ms, TrainError:0.0014748445, TrainErrorChange:-6.9849193E-10, TrainAccuracy: 0.8807947
Epoch:99211, Time:0ms, TrainError:0.0014748435, TrainErrorChange:-1.0477379E-9, TrainAccuracy: 0.8807947
Epoch:99212, Time:0ms, TrainError:0.0014748441, TrainErrorChange:5.820766E-10, TrainAccuracy: 0.8807947
Epoch:99213, Time:1ms, TrainError:0.0014748434, TrainErrorChange:-6.9849193E-10, TrainAccuracy: 0.8807947
Epoch:99214, Time:0ms, TrainError:0.0014748428, TrainErrorChange:-5.820766E-10, TrainAccuracy: 0.8807947
Epoch:99215, Time:1ms, TrainError:0.0014748432, TrainErrorChange:4.656613E-10, TrainAccuracy: 0.8807947
Epoch:99216, Time:0ms, TrainError:0.0014748431, TrainErrorChange:-1.1641532E-10, TrainAccuracy: 0.8807947
Epoch:99217, Time:1ms, TrainError:0.0014748429, TrainErrorChange:-2.3283064E-10, TrainAccuracy: 0.8807947
Epoch:99218, Time:0ms, TrainError:0.0014748432, TrainE

Epoch:99288, Time:0ms, TrainError:0.0014748224, TrainErrorChange:-1.6298145E-9, TrainAccuracy: 0.8807947
Epoch:99289, Time:0ms, TrainError:0.0014748228, TrainErrorChange:3.4924597E-10, TrainAccuracy: 0.8807947
Epoch:99290, Time:0ms, TrainError:0.0014748239, TrainErrorChange:1.1641532E-9, TrainAccuracy: 0.8807947
Epoch:99291, Time:1ms, TrainError:0.0014748235, TrainErrorChange:-4.656613E-10, TrainAccuracy: 0.8807947
Epoch:99292, Time:0ms, TrainError:0.0014748226, TrainErrorChange:-8.1490725E-10, TrainAccuracy: 0.8807947
Epoch:99293, Time:1ms, TrainError:0.0014748228, TrainErrorChange:1.1641532E-10, TrainAccuracy: 0.8807947
Epoch:99294, Time:0ms, TrainError:0.0014748231, TrainErrorChange:3.4924597E-10, TrainAccuracy: 0.8807947
Epoch:99295, Time:1ms, TrainError:0.0014748226, TrainErrorChange:-4.656613E-10, TrainAccuracy: 0.8807947
Epoch:99296, Time:0ms, TrainError:0.0014748226, TrainErrorChange:0.0, TrainAccuracy: 0.8807947
Epoch:99297, Time:1ms, TrainError:0.0014748225, TrainErrorChange:

Epoch:99367, Time:0ms, TrainError:0.0014748003, TrainErrorChange:5.820766E-10, TrainAccuracy: 0.8807947
Epoch:99368, Time:0ms, TrainError:0.0014747995, TrainErrorChange:-8.1490725E-10, TrainAccuracy: 0.8807947
Epoch:99369, Time:0ms, TrainError:0.0014747989, TrainErrorChange:-5.820766E-10, TrainAccuracy: 0.8807947
Epoch:99370, Time:1ms, TrainError:0.0014747996, TrainErrorChange:6.9849193E-10, TrainAccuracy: 0.8807947
Epoch:99371, Time:0ms, TrainError:0.0014747984, TrainErrorChange:-1.1641532E-9, TrainAccuracy: 0.8807947
Epoch:99372, Time:1ms, TrainError:0.001474798, TrainErrorChange:-4.656613E-10, TrainAccuracy: 0.8807947
Epoch:99373, Time:0ms, TrainError:0.0014747984, TrainErrorChange:4.656613E-10, TrainAccuracy: 0.8807947
Epoch:99374, Time:1ms, TrainError:0.0014747987, TrainErrorChange:2.3283064E-10, TrainAccuracy: 0.8807947
Epoch:99375, Time:0ms, TrainError:0.0014747976, TrainErrorChange:-1.0477379E-9, TrainAccuracy: 0.8807947
Epoch:99376, Time:1ms, TrainError:0.0014747982, TrainErro

Epoch:99446, Time:0ms, TrainError:0.0014747747, TrainErrorChange:-1.1641532E-10, TrainAccuracy: 0.8807947
Epoch:99447, Time:0ms, TrainError:0.0014747753, TrainErrorChange:5.820766E-10, TrainAccuracy: 0.8807947
Epoch:99448, Time:0ms, TrainError:0.0014747744, TrainErrorChange:-8.1490725E-10, TrainAccuracy: 0.8807947
Epoch:99449, Time:0ms, TrainError:0.001474774, TrainErrorChange:-4.656613E-10, TrainAccuracy: 0.8807947
Epoch:99450, Time:0ms, TrainError:0.001474774, TrainErrorChange:0.0, TrainAccuracy: 0.8807947
Epoch:99451, Time:0ms, TrainError:0.0014747735, TrainErrorChange:-4.656613E-10, TrainAccuracy: 0.8807947
Epoch:99452, Time:1ms, TrainError:0.0014747743, TrainErrorChange:8.1490725E-10, TrainAccuracy: 0.8807947
Epoch:99453, Time:0ms, TrainError:0.0014747734, TrainErrorChange:-9.313226E-10, TrainAccuracy: 0.8807947
Epoch:99454, Time:1ms, TrainError:0.0014747732, TrainErrorChange:-2.3283064E-10, TrainAccuracy: 0.8807947
Epoch:99455, Time:0ms, TrainError:0.0014747732, TrainErrorChange:

## Evaluating the model

In [231]:
EvaluationMetrics pm = Evaluators.evaluateRegressor(neuralNet, trainAndTestSet[1]);
System.out.println(pm);

RSquared: 0.8268303
MeanSquaredError: 0.005913385
ResidualStandardError: 0.07728399
FStatistics: 68.681984



## Run raw and untested data aginst the model

In [232]:
var tensor_untrained = Tensor.create(inputsNum, outputsNum, new float[] {
    0.00632f,18.00f,2.310f,0,0.5380f,6.5750f,65.20f,4.0900f,1,296.0f,15.30f,396.90f,4.98f
});

tensor_untrained.div(normalizer.getMaxInputs());
neuralNet.setInput(tensor_untrained);

System.out.println(
    "Predicted price of the house is for 1 (untrained) :" 
    + neuralNet.getOutput()[0] * normalizer.getMaxOutputs().get(0)
);

Predicted price of the house is for 1 (untrained) :24.614645


## Save the model

In [14]:
var EXPORT_PATH = "/tmp/BostonHouseRegressor.dnet";
System.out.println("[+] Saving the model to: " + EXPORT_PATH);
FileIO.writeToFile(neuralNet, EXPORT_PATH);

[+] Saving the model to: /tmp/BostonHouseRegressor.dnet


## Import the model

In [14]:
System.out.println("[+] Importing the model from: " + EXPORT_PATH);
ConvolutionalNetwork neuralNet;
try (ObjectInputStream ois = new ObjectInputStream(new FileInputStream(EXPORT_PATH))) {
    neuralNet = ConvolutionalNetwork.class.cast(ois.readObject()) ;
}

[+] Importing the model from: /tmp/DukeClassifier.dnet
